In [1]:
import sys
sys.path.append("..//src")
import os
import datetime
import pandas as pd
import numpy as np
from example_lorenz import get_lorenz_data
from sindy_utils import library_size
import training
import torch
print(torch.cuda.is_available())


True


# Generate data

In [2]:

# generate training, validation, testing data
noise_strength = 1e-6
training_data = get_lorenz_data(1024, noise_strength=noise_strength)
validation_data = get_lorenz_data(20, noise_strength=noise_strength)
training_data['x'] = torch.tensor(training_data['x']).float().to('cuda')
training_data['dx'] = torch.tensor(training_data['dx']).float().to('cuda')
training_data['t'] = torch.tensor(training_data['t']).float().to('cuda')
training_data['z'] = torch.tensor(training_data['z']).float().to('cuda')
training_data['dz'] = torch.tensor(training_data['dz']).float().to('cuda')
training_data['ddx'] = None

validation_data['x'] = torch.tensor(validation_data['x']).float().to('cuda')
validation_data['dx'] = torch.tensor(validation_data['dx']).float().to('cuda')
validation_data['t'] = torch.tensor(validation_data['t']).float().to('cuda')
validation_data['z'] = torch.tensor(validation_data['z']).float().to('cuda')
validation_data['dz'] = torch.tensor(validation_data['dz']).float().to('cuda')
validation_data['ddx'] = None


# Set up model and training parameters

In [3]:
params = {}

params['input_dim'] = 128
params['latent_dim'] = 3
params['model_order'] = 1
params['poly_order'] = 3
params['include_sine'] = False
params['library_dim'] = library_size(params['latent_dim'], params['poly_order'], params['include_sine'], True)

# sequential thresholding parameters
params['sequential_thresholding'] = True
params['coefficient_threshold'] = 0.1
params['threshold_frequency'] = 1000
params['coefficient_mask'] = torch.ones((params['library_dim'], params['latent_dim']))
params['coefficient_initialization'] = 'constant'

# loss function weighting
params['loss_weight_decoder'] = 1.0
params['loss_weight_sindy_z'] = 0
params['loss_weight_sindy_x'] = 1e-4
params['loss_weight_sindy_regularization'] = 1e-5

params['activation'] = 'sigmoid'
params['widths'] = [64, 32]
print(params['widths'][::-1])
# training parameters
params['epoch_size'] = training_data['x'].shape[0]
params['batch_size'] = 1024
params['learning_rate'] = 5e-4

params['data_path'] = os.getcwd() + '/'
params['print_progress'] = True
params['print_frequency'] = 1

# training time cutoffs
params['max_epochs'] = 5001
params['refinement_epochs'] = 1001

[32, 64]


In [4]:
import numpy as np
import torch

def to_numpy(obj):
    if isinstance(obj, torch.Tensor):
        return obj.cpu().numpy()  # Convert tensor to numpy array
    elif isinstance(obj, dict):
        return {k: to_numpy(v) for k, v in obj.items()}  # Apply recursively to dictionaries
    elif isinstance(obj, list):
        return [to_numpy(v) for v in obj]  # Apply recursively to lists
    else:
        return obj  # Return the object as is if it's neither a tensor, list, nor dictionary


# Run training experiments

In [5]:
num_experiments = 1
df = pd.DataFrame()
for i in range(num_experiments):
    print('EXPERIMENT %d' % i)


    params['coefficient_mask'] = torch.ones((params['library_dim'], params['latent_dim']))

    params['save_name'] = 'lorenz_' + datetime.datetime.now().strftime("%Y_%m_%d_%H_%M_%S_%f")
    
    results_dict = training.train_network(training_data, validation_data, params)
    results_dict = to_numpy(results_dict)
    params = to_numpy(params)

    df = df._append({**results_dict, **params}, ignore_index=True)

df.to_pickle('experiment_results_' + datetime.datetime.now().strftime("%Y%m%d%H%M") + '.pkl')

EXPERIMENT 0
Device: cuda:0


c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:181: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'x': torch.tensor(data['x'][idxs], dtype=torch.float32).to(params['device']),
c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:182: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'dx': torch.tensor(data['dx'][idxs], dtype=torch.float32).to(params['device']),
c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:188: UserW

TRAINING
Epoch 0
   Training Total Loss: 0.07790491729974747
   Training decoder Loss: 0.07627654075622559
   Training sindy_z Loss: 6450.06201171875
   Training sindy_x Loss: 16.195486068725586
   Training sindy_regularization Loss: 0.8826998472213745
   Validation Total Loss: 0.08071061223745346
   Validation decoder Loss: 0.07908347994089127
   Validation sindy_z Loss: 5099.42578125
   Validation sindy_x Loss: 16.183034896850586
   Validation sindy_regularization Loss: 0.8826998472213745
Decoder Loss Ratio: 0.414947, Decoder SINDy Loss Ratio: 1.146118
Epoch 1
   Training Total Loss: 0.039002299308776855
   Training decoder Loss: 0.03749050945043564
   Training sindy_z Loss: 502.5606994628906
   Training sindy_x Loss: 15.037206649780273
   Training sindy_regularization Loss: 0.8068941831588745
   Validation Total Loss: 0.03881099820137024
   Validation decoder Loss: 0.03728275001049042
   Validation sindy_z Loss: 482.15704345703125
   Validation sindy_x Loss: 15.201786994934082
   Va

c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:59: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  loss_val, _, _ = autoencoder_network.define_loss(torch.tensor(train_dict['x'], dtype=torch.float32), torch.tensor(train_dict['dx'], dtype=torch.float32), train_dict['ddx'], params=params)


Epoch 0
   Training Total Loss: 9.058027899300214e-06
   Training decoder Loss: 1.8947984017358976e-06
   Training sindy_z Loss: 3.1543350219726562
   Training sindy_x Loss: 0.007792262826114893
   Training sindy_regularization Loss: 0.6384003758430481
   Validation Total Loss: 9.674397915659938e-06
   Validation decoder Loss: 2.622071178848273e-06
   Validation sindy_z Loss: 2.7587430477142334
   Validation sindy_x Loss: 0.006683234125375748
   Validation sindy_regularization Loss: 0.6384003758430481
Decoder Loss Ratio: 0.000014, Decoder SINDy Loss Ratio: 0.000473
Epoch 1
Epoch 1
   Training Total Loss: 7.929703315312508e-06
   Training decoder Loss: 9.77293098003429e-07
   Training sindy_z Loss: 3.132542371749878
   Training sindy_x Loss: 0.005676622502505779
   Training sindy_regularization Loss: 0.6384748220443726
   Validation Total Loss: 7.601726338180015e-06
   Validation decoder Loss: 7.493330258512287e-07
   Validation sindy_z Loss: 2.719881772994995
   Validation sindy_x Loss

c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:73: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  loss_val, final_losses, _ = autoencoder_network.define_loss(torch.tensor(validation_dict['x'], dtype=torch.float32), torch.tensor(validation_dict['dx'], dtype=torch.float32),validation_dict['ddx'], params=params)
c:\Users\ianma\Desktop\Study\Python\CS4240_DeepLearning_Group41_ReproducibilityProject\Autoencoders-Reproduction\examples\..//src\training.py:75: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  _, _, _, _, _, _, _, sindy_predict = autoencoder_network(torch.tensor(validation_dict['x'], dtype=t

In [6]:
print(results_dict)
    
print(params)

{'num_epochs': 5000, 'x_norm': array(0.19058712, dtype=float32), 'sindy_predict_norm_x': array(14.119863, dtype=float32), 'sindy_predict_norm_z': 249.47607421875, 'sindy_coefficients': array([[ 4.1558026e-04,  5.5582709e+00, -5.4355423e-05],
       [-8.6722612e+00,  2.4685913e-04,  4.6121440e-04],
       [ 7.1371289e-04, -1.8874544e+00,  7.1764407e-05],
       [ 9.2299118e+00, -1.3897810e-05, -2.2197631e-03],
       [-3.0030977e-04,  1.7698955e-04,  2.3767787e-05],
       [ 3.4067131e-04,  1.4002995e-05,  8.5998011e+00],
       [-3.3702835e-04, -2.6530986e+00,  1.5834039e-03],
       [-7.1569963e-04,  3.6923768e-04, -4.5062864e-04],
       [-4.2423955e-03,  2.4669222e-04,  1.1099468e-01],
       [-1.4130692e-03, -4.2012829e-02,  8.3985046e-04],
       [-3.6562737e-02, -5.6107691e-04, -3.9566077e-02],
       [-2.9170725e-03, -4.4516346e-04, -1.4516333e-04],
       [-2.4809275e-02, -1.0196185e-03,  3.0469589e-03],
       [-4.1166362e-03, -2.7241826e-04, -1.6127054e-01],
       [ 2.479620